In [1]:
from __future__ import print_function

import os
import mat73
import numpy as np
import matplotlib.pyplot as plt
import scipy.io as scio
import torch
import torch.optim
from skimage.metrics import peak_signal_noise_ratio as compare_psnr
from skimage.metrics import structural_similarity as compare_ssim

# from architecture import MST
torch.cuda.manual_seed(seed=666)
torch.backends.cudnn.enabled = True
torch.backends.cudnn.benchmark = True
dtype = torch.cuda.FloatTensor
device = torch.device('cuda')
torch.cuda.manual_seed(seed=666)

########################################### 辅助函数 ###########################################
def thres_21(L, tau, M, N, B):
    S = torch.sqrt(torch.sum(torch.mul(L, L), 2))
    S[S == 0] = 1
    T = 1 - tau / S
    T[T < 0] = 0
    R = T.reshape(M, N, 1).repeat((1, 1, B))
    res = torch.mul(R, L)
    return res


################################ 读取数据 ################################
YY= mat73.loadmat("./Data/T31UDQ/T31UDQ_20m_raw1.mat")['T31UDQ_20m_raw1'] 
YY = np.double(YY)
YY = YY/YY.max()
Mask1_500 = mat73.loadmat("./Data/Mask1_500.mat")['Mask1_500']
Mask2_500 = mat73.loadmat("./Data/Mask2_500.mat")['Mask2_500']

Mask = np.copy(Mask2_500)
Mask[ Mask != 0 ] = 1
# Test1_Clean是干净图像，取的是4，2，0三个时相
Test1_Clean = np.copy(YY[:, :, :, [4, 2, 0]])

# 生成云图YY，含有6个时相
Clean = YY[:, :, :, [4, 2, 0, 5, 3, 1]]
YY = np.multiply((1 - Mask), (YY[:, :, :, [4, 2, 0, 5, 3, 1]])) + Mask
Noisy = np.copy(YY)
Cloud = np.copy(Mask)
Mask = 1 - Cloud
###########################################################################

M, N, B, T = Noisy.shape
Clean = torch.from_numpy(Clean.reshape(M, N, B, T)).to(device)
Mask = torch.from_numpy(Mask.reshape(M, N, B, T)).to(device)  # 云=0
Cloud = torch.from_numpy(Cloud.reshape(M, N, B, T)).to(device)  # 云=1
Noisy = torch.from_numpy(Noisy.reshape(M, N, B, T)).to(device)


################################ 全局设置 ################################
def grid_combine(args_list):
    for rate in args_list[0]:
        for lambda2 in args_list[1]:
            for rho in args_list[2]:
                for alpha in args_list[3]:
                    if rate == 125 and rho ==0.08 and alpha==1.03 :
                        continue
                    yield rate, lambda2, rho, alpha
args_list = [
    [25, 30, 35, 40, 45, 50, 60],  # rate
    [0.5, 0.4, 0.6],  # lambda2
    [0.01, 0.05, 0.1, 0.15, 0.2, 0.25, 0.3, 0.35, 0.4, 0.45, 0.5],  # rho
    [1]  # alpha
]
condidates = [
    # lambda1, lambda2, rho
    # [6.0, 0.1, 0.12, 1.03]     # condidate2
    # [12.5, 0.1, 0.1], 
    # [10.0, 0.1, 0.1], 
    # [7.50, 0.1, 0.1],  
    # [10.0, 0.2, 0.1], 
    # [10.0, 0.4, 0.1], 
]
condidates = [
    # rate, lambda2, rho, alpha
    # [90, 0.06, 0.06, 1.03],
    # [95, 0.06, 0.08, 1.03],
    # [88, 0.06, 0.08, 1.03],
    # [90, 0.08, 0.08, 1.03],
    # [30, 0.4, 0.06, 1.0],
    [60, 0.4, 0.06, 1.02],
    [60, 0.2, 0.06, 1.03],
    [50, 0.4, 0.06, 1.03],
]
iter_num, epoch_num = 150, 300
order = 0
# for rate, lambda2, rho, alpha in condidates:
for rate, lambda2, rho, alpha in grid_combine(args_list):
    # rate = lambda1 / rho
    lambda1 = rate * rho
    iters = 0
    order += 1
    log_dir = "./model3-picardie-acc/order[%03d]-iter[%3d]-epoch[%3d]-rate[%.3f]-lambda2[%.3f]-rho[%.3f,%.3f]" \
              % (order, iter_num, epoch_num, rate, lambda2, rho, alpha)
    if not os.path.exists(log_dir):
        os.makedirs(log_dir)
    else:
        continue
    # rate, lambda2, rho, alpha = 125, 0.1, 0.08, 1.04
    ################################ 初始化 ################################
    Y = Noisy.clone()
    X = Noisy.clone()
    W = Noisy.clone()
    C = torch.zeros(Y.shape).type(dtype).to(device)
    M_updata = Mask.clone()
    # model = MST(dim=B*T, stage=2, num_blocks=[2, 2, 2]).cuda()
    psnr1 = 0
    s0_min = 10000
    ################################ 子问题更新 ################################
    while iters < iter_num:
        if iters >= 100 and psnr1 < 43:
            break
        iters += 1
        ################################ 更新子问题X ################################

        X = (torch.mul(M_updata, (Y - C)) + rho * W ) / (M_updata + rho)

        ################################ 更新子问题W ################################
        U, s, VH = torch.linalg.svd(X.reshape(M * N, B * T), full_matrices=False)  # B*T, M*N
        s0 = s[0]
        rho *= alpha
        # if s0<s0_min: # s0处于不断下降的第一阶段
        #     s0_min = s0
        #     rho *= alpha
        # else:
        #     rho *= 1.02
        rate = lambda1 / rho
        print("s: ", s)
        s = s - lambda1 / rho
        s[s < 0] = 0
        S = torch.diag(s)
        W = torch.mm(torch.mm(U, S), VH).reshape(M, N, B, T)
        ################################ 更新子问题C ################################
        L = Y - torch.mul(X, M_updata)
        for t in range(T):
            C[:, :, :, t] = thres_21(L[:, :, :, t], lambda2, M, N, B)

        ################################ 更新掩码M ################################
        # B_mean = torch.mean(Y-X, dim=2).reshape(M, N, 1, T).repeat((1, 1, B, 1))
        # M_updata[:, :, :, :3][torch.abs(B_mean[:, :, :, :3]) > 0.01] = 0   # M_update=1表示无云，M_update=0表示云
        # if iters > 5:
        #     M_updata[:, :, :, :3][torch.abs(B_mean[:, :, :, :3]) < 0.01] = 1

        ################################ 进行指标评估 ################################
        # mse = torch.sum((X - Clean) ** 2)
        psnr = []
        for t in range(3):
            psnr_t = 0
            for b in range(B):
                psnr_t += compare_psnr(X[:, :, b, t].detach().cpu().numpy(), Clean[:, :, b, t].detach().cpu().numpy(), data_range=1)
            psnr.append(psnr_t / B)
        ssim = []
        for t in range(3):
            ssim_b = 0
            for b in range(B):
                ssim_b += compare_ssim(X[:, :, b, t].detach().cpu().numpy(), Clean[:, :, b, t].detach().cpu().numpy())
            ssim.append(ssim_b / B)
        # print("The %03dth iters, the %03dth epoch, loss: %.5f, mse: %.5f, psnr: %.5f, ssim: %.5f" % (
        #     iters, epoch, loss.item(), mse, psnr, ssim))

        image_Clean = Clean.cpu().numpy()
        image_Y = Y.cpu().numpy()
        image_X = X.cpu().detach().numpy()
        image_C = C.cpu().numpy()
        image_M = M_updata.cpu().numpy()
        plt.figure(figsize=(20, 20))
        for i in range(6):
            plt.subplot(6, 6, 1 + i)
            plt.title("Clean")
            plt.imshow(image_Clean[:, :, [4, 2, 0], i]*5)
            plt.axis('off')

            plt.subplot(6, 6, 7 + i)
            plt.title("X")
            plt.imshow(image_X[:, :, [4, 2, 0], i]*5)
            plt.axis('off')

            plt.subplot(6, 6, 13 + i)
            plt.title("Y")
            plt.imshow(image_Y[:, :, [4, 2, 0], i]*5)
            plt.axis('off')

            plt.subplot(6, 6, 19 + i)
            plt.title("Y-X")
            plt.imshow(image_Y[:, :, [4, 2, 0], i]*5 - image_X[:, :, [4, 2, 0], i]*5)
            plt.axis('off')

            plt.subplot(6, 6, 25 + i)
            plt.title("C")
            plt.imshow(image_C[:, :, 0, i]*5, cmap='gray')
            plt.axis('off')

            plt.subplot(6, 6, 31 + i)
            plt.title("M_update")
            plt.imshow(image_M[:, :, 0, i], cmap='gray')
            plt.axis('off')
        psnr1, psnr2, psnr3 = psnr
        ssim1, ssim2, ssim3 = ssim
        result_path = "%s/iter[%03d]-pnsr[%.3f, %.3f, %.3f]-ssim[%.3f, %.3f, %.3f]-s0, rate[%.3f, %.2f].png" % (
            log_dir, iters, psnr1, psnr2, psnr3, ssim1, ssim2, ssim3, s0, rate)
        plt.savefig(result_path)
        plt.clf()

        plt.close()
        scio.savemat("%s/recover_data.mat" % log_dir, {"recover_data": image_X})
    # decrease = True
    # up = False


s:  tensor([9.5524e+02, 4.4211e+02, 2.8481e+02, 1.1002e+02, 3.0043e+01, 1.1176e+01,
        7.2604e+00, 6.7541e+00, 6.3818e+00, 5.9482e+00, 4.6524e+00, 3.5363e+00,
        3.2869e+00, 2.5639e+00, 2.0778e+00, 1.5974e+00, 1.4025e+00, 1.3302e+00,
        1.1720e+00, 1.1325e+00, 1.0083e+00, 9.5676e-01, 8.8149e-01, 8.1024e-01,
        7.5993e-01, 7.2015e-01, 7.0297e-01, 6.7027e-01, 6.2974e-01, 5.8175e-01,
        5.7207e-01, 5.5201e-01, 5.1008e-01, 4.7857e-01, 4.0359e-01, 3.0167e-01],
       device='cuda:0', dtype=torch.float64)


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

s:  tensor([9.2128e+02, 4.1498e+02, 2.6319e+02, 1.0559e+02, 2.6135e+01, 9.7320e+00,
        6.2367e+00, 5.8711e+00, 5.4074e+00, 4.9237e+00, 3.7007e+00, 2.9892e+00,
        2.7495e+00, 2.1921e+00, 1.7462e+00, 1.3762e+00, 1.1606e+00, 1.1281e+00,
        1.0069e+00, 9.7085e-01, 8.7929e-01, 8.1493e-01, 7.5512e-01, 7.0421e-01,
        6.7336e-01, 6.2212e-01, 6.1170e-01, 5.8300e-01, 5.5160e-01, 4.9980e-01,
        4.8495e-01, 4.7751e-01, 4.4450e-01, 4.1577e-01, 3.4991e-01, 2.6089e-01],
       device='cuda:0', dtype=torch.float64)


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

s:  tensor([8.8685e+02, 3.8832e+02, 2.4296e+02, 1.0430e+02, 2.6131e+01, 9.7294e+00,
        6.2384e+00, 5.8720e+00, 5.4098e+00, 4.9327e+00, 3.7074e+00, 2.9942e+00,
        2.7512e+00, 2.1926e+00, 1.7516e+00, 1.3785e+00, 1.1627e+00, 1.1298e+00,
        1.0069e+00, 9.7243e-01, 8.7981e-01, 8.1503e-01, 7.5664e-01, 7.0456e-01,
        6.7369e-01, 6.2252e-01, 6.1159e-01, 5.8300e-01, 5.5176e-01, 5.0003e-01,
        4.8676e-01, 4.7829e-01, 4.4540e-01, 4.1582e-01, 3.5008e-01, 2.6094e-01],
       device='cuda:0', dtype=torch.float64)


...

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

s:  tensor([8.7497e+02, 3.7978e+02, 2.3725e+02, 1.0658e+02, 2.8622e+01, 1.0655e+01,
        6.8344e+00, 6.4315e+00, 5.9292e+00, 5.4131e+00, 4.0712e+00, 3.2858e+00,
        3.0162e+00, 2.4026e+00, 1.9224e+00, 1.5107e+00, 1.2756e+00, 1.2387e+00,
        1.1031e+00, 1.0665e+00, 9.6394e-01, 8.9327e-01, 8.2987e-01, 7.7180e-01,
        7.3794e-01, 6.8213e-01, 6.6981e-01, 6.3852e-01, 6.0440e-01, 5.4779e-01,
        5.3421e-01, 5.2420e-01, 4.8805e-01, 4.5547e-01, 3.8350e-01, 2.8586e-01],
       device='cuda:0', dtype=torch.float64)


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

s:  tensor([8.3478e+02, 3.4897e+02, 2.1463e+02, 1.0525e+02, 2.8624e+01, 1.0651e+01,
        6.8347e+00, 6.4324e+00, 5.9301e+00, 5.4169e+00, 4.0740e+00, 3.2905e+00,
        3.0182e+00, 2.4027e+00, 1.9259e+00, 1.5137e+00, 1.2767e+00, 1.2420e+00,
        1.1034e+00, 1.0670e+00, 9.6406e-01, 8.9342e-01, 8.3114e-01, 7.7209e-01,
        7.3792e-01, 6.8245e-01, 6.6973e-01, 6.3853e-01, 6.0441e-01, 5.4834e-01,
        5.3751e-01, 5.2457e-01, 4.8865e-01, 4.5551e-01, 3.8365e-01, 2.8584e-01],
       device='cuda:0', dtype=torch.float64)


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i